In [ ]:
!pip install -Uq albumentations trackio datasets

# need to install the source version of transformers for DinoV3 backbone
!pip install git+https://github.com/huggingface/transformers

In [ ]:
from transformers import DetrConfig, DetrForObjectDetection, AutoImageProcessor, Trainer, TrainingArguments, pipeline
from datasets import load_dataset
import albumentations as A
import numpy as np
import torch
from PIL import Image, ImageDraw, ImageFont
import json
import os
import subprocess
from datasets import DatasetDict, Dataset, Features, Value, Sequence, ClassLabel
from datasets import Image as DatasetImage

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
!unzip "/content/drive/MyDrive/AIC Data/Project/Algae.v6i.coco.zip" -d "/content/drive/MyDrive/AIC Data/Project/dataset"

# Prepping

In [ ]:
# directories
coco_root = "/content/drive/MyDrive/AIC Data/Project/dataset"
output_root = "/content/drive/MyDrive/AIC Data/Project/algae-detr-dinov3"

In [ ]:
# dinov3 licensing
from huggingface_hub import login
login(token='')

In [ ]:
# assign id and labels -> used in model config
num_labels = []
id2label = {}
label2id = {}

coco_root = "/content/drive/MyDrive/AIC Data/Project/dataset"
with open(coco_root + "/train/_annotations.coco.json", "r") as f:
    data = json.load(f)
    categories = data['categories']
    # categories.pop(0) # remove plant as a category
    for item in categories:
        item_id = item['id'] #- 1  # shift ids left by 1
        item_label = item['name']

        id2label[item_id] = item_label

        if item_label in label2id:
            label2id[item_label].append(item_id)
        else:
            label2id[item_label] = item_id

print(len(id2label))
print(id2label)
print(label2id)

19
{0: 'plants', 1: 'Algae', 2: 'Clam Shell', 3: 'Elodea Canadensis', 4: 'Eriocaulon Septangulare', 5: 'I. Lacustris', 6: 'Leaves', 7: 'M. Spicatum', 8: 'M. Tenellum', 9: 'Najas', 10: 'P. Amplifolius', 11: 'P. Gramineus', 12: 'P. Perfoliatus', 13: 'P. Praelongus', 14: 'P. Robbinsii', 15: 'P. Zosteriformis', 16: 'Snail', 17: 'Unknown Plant', 18: 'Vallisneria Americana'}
{'plants': 0, 'Algae': 1, 'Clam Shell': 2, 'Elodea Canadensis': 3, 'Eriocaulon Septangulare': 4, 'I. Lacustris': 5, 'Leaves': 6, 'M. Spicatum': 7, 'M. Tenellum': 8, 'Najas': 9, 'P. Amplifolius': 10, 'P. Gramineus': 11, 'P. Perfoliatus': 12, 'P. Praelongus': 13, 'P. Robbinsii': 14, 'P. Zosteriformis': 15, 'Snail': 16, 'Unknown Plant': 17, 'Vallisneria Americana': 18}


In [ ]:
# model -> https://huggingface.co/docs/transformers/main/en/tasks/training_vision_backbone
config = DetrConfig(backbone="facebook/dinov3-convnext-large-pretrain-lvd1689m",
                    use_pretrained_backbone=True, use_timm_backbone=False,
                    num_labels=len(id2label), id2label=id2label, label2id=label2id)
model = DetrForObjectDetection(config)

for param in model.model.backbone.parameters():
    param.requires_grad = False
image_processor = AutoImageProcessor.from_pretrained("facebook/detr-resnet-50")

Loading weights:   0%|          | 0/340 [00:00<?, ?it/s]

DINOv3ConvNextBackbone LOAD REPORT from: facebook/dinov3-convnext-large-pretrain-lvd1689m
Key               | Status     |  | 
------------------+------------+--+-
layer_norm.weight | UNEXPECTED |  | 
layer_norm.bias   | UNEXPECTED |  | 

Notes:
- UNEXPECTED	:can be ignored when loading from different task/architecture; not ok if you expect identical arch.


In [ ]:
# coco dataset loader modified from https://discuss.huggingface.co/t/load-a-coco-format-database-from-disk-for-detr/153752/2
subprocess.check_call(["pip", "install", "datasets"])

class CocoDatasetLoader:
    def __init__(self, coco_folder):
        self.coco_folder = coco_folder

    def group_by_key_id(self, data, key_id, category_id_to_index):
        """
        Groups data by a specified key and maps category IDs to indices.

        Args:
            data (list): List of dictionaries containing the data.
            key_id (str): The key to group by.
            category_id_to_index (dict): Mapping from category IDs to indices.

        Returns:
            dict: Grouped data.
        """
        grouped_data = {}
        for item in data:
            key_value = item[key_id]
            if key_value not in grouped_data:
                grouped_data[key_value] = {k: [] for k in item.keys() if k != key_id}
            for k, v in item.items():
                if k != key_id:
                    grouped_data[key_value][k].append(v)
            grouped_data[key_value]['category'] = [category_id_to_index[x] for x in grouped_data[key_value]['category_id']]
        return grouped_data

    def load_coco_hf_dataset(self, split):
        """
        Loads COCO dataset and processes it into a format suitable for Hugging Face datasets.

        Args:
            split (str): Dataset split (e.g., 'Train', 'Test', 'Validation').

        Returns:
            Dataset: HuggingFace Dataset of the split of COCO dataset.
        """
        # Load the JSON file
        json_file_path = os.path.join(self.coco_folder, f'{split}/_annotations.coco.json')
        try:
            with open(json_file_path, 'r') as f:
                coco_data = json.load(f)
        except FileNotFoundError:
            print(f"File not found: {json_file_path}")
            return []

        # Extract category names and create a mapping from category IDs to indices
        category_names = [cat['name'] for cat in coco_data['categories']]
        category_id_to_index = {cat['id']: category_names[idx] for idx, cat in enumerate(coco_data['categories'])}

        # Group annotations by 'image_id'
        grouped_annotations = self.group_by_key_id(coco_data['annotations'], 'image_id', category_id_to_index)

        # Create a dictionary of images
        grouped_images = {item['id']: item for item in coco_data['images']}

        # Initialize 'objects' field in grouped_images
        annotations_keys = list(grouped_annotations.values())[0].keys()
        for k, v in grouped_images.items():
            grouped_images[k]['objects'] = {key: [] for key in annotations_keys}

        # Populate 'objects' field with annotations
        for k, v in grouped_annotations.items():
            grouped_images[k]['objects'] = v

        # Add image paths and IDs
        for k, v in grouped_images.items():
            v['image'] = os.path.join(self.coco_folder, split, v['file_name'])
            v['image_id'] = v['id']

        # Create a Hugging Face dataset from the custom data using from_list for efficiency
        hf_dataset = Dataset.from_list(list(grouped_images.values()))
        print(list(grouped_images.values()))
        print(hf_dataset)

        # Define the features for the main dataset
        features = Features({
            'id': Value('int64'),
            'license': Value('string'),
            'file_name': Value('string'),
            'height': Value('int64'),
            'width': Value('int64'),
            'date_captured': Value('string'),
            'extra': {
                'user_tags': Sequence(Value('string')),
                'name': Value('string')
            },
            'objects': Sequence({
                'id': Value('int64'),
                'category_id': Value('int64'),
                'bbox': Sequence(Value('float32')),
                'area': Value('float32'),
                'segmentation': Sequence(Value('int64')),
                'iscrowd': Value('int64'),
                'category': Value('string')
            }),
            'image': DatasetImage(),
            'image_id': Value('int64')
        })

        # Cast the features for the Hugging Face dataset
        hf_dataset = hf_dataset.cast(features)

        return hf_dataset

In [ ]:
# load dataset
coco_loader = CocoDatasetLoader(coco_folder=coco_root)

hf_dataset_dict = DatasetDict()
for split in ['train', 'test', 'valid']:
    hf_dataset = coco_loader.load_coco_hf_dataset(split)
    print(f"Dataset for {split} split:")
    print(hf_dataset)
    hf_dataset_dict[split.lower()] = hf_dataset

[{'id': 0, 'license': 1, 'file_name': 'frame810_810966ms_jpg.rf.cd7aaa3b41f7c024243d883419cd45dd.jpg', 'height': 1080, 'width': 1920, 'date_captured': '2025-11-24T02:48:19+00:00', 'extra': {'user_tags': ['SUNSET_2025-06-13_15.17.00.006'], 'name': 'frame810_810966ms.jpg'}, 'objects': {'id': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22], 'category_id': [10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 17], 'bbox': [[635, 111, 62, 133], [616, 245, 119, 108], [772, 377, 82, 94], [846, 470, 131, 88], [782, 659, 97, 94], [661, 571, 124, 173], [542, 685, 9, 8], [403, 454, 110, 179], [499, 401, 184, 122], [587, 330, 74, 103], [478, 296, 69, 70], [533, 625, 153, 164], [289, 725, 106, 92], [424, 872, 75, 71], [485, 939, 110, 107], [78, 489, 143, 197], [1042, 880, 75, 74], [1282, 703, 68, 71], [1513, 580, 125, 127], [1573, 172, 138, 92], [1131, 333, 92, 140], [1690, 499, 198, 392]], 'area': [8246, 12852, 7708, 11528, 9118, 21452

Casting the dataset:   0%|          | 0/1930 [00:00<?, ? examples/s]

Dataset for train split:
Dataset({
    features: ['id', 'license', 'file_name', 'height', 'width', 'date_captured', 'extra', 'objects', 'image', 'image_id'],
    num_rows: 1930
})
[{'id': 0, 'license': 1, 'file_name': 'frame83_83966ms_jpg.rf.c60084ecf0eb3ce442a057ec8fb1123e.jpg', 'height': 1080, 'width': 1920, 'date_captured': '2025-11-24T02:48:19+00:00', 'extra': {'user_tags': ['LGV_2025-06-13_17.21.18.020_cont'], 'name': 'frame83_83966ms.jpg'}, 'objects': {'id': [1, 2, 3, 4], 'category_id': [1, 18, 18, 18], 'bbox': [[25, 552, 289, 327], [313, 42, 545, 607], [999, 278, 181, 153], [882, 24, 160, 121]], 'area': [94503, 330815, 27693, 19360], 'segmentation': [[], [], [], []], 'iscrowd': [0, 0, 0, 0], 'category': ['Algae', 'Vallisneria Americana', 'Vallisneria Americana', 'Vallisneria Americana']}, 'image': '/content/drive/MyDrive/AIC Data/Project/dataset/test/frame83_83966ms_jpg.rf.c60084ecf0eb3ce442a057ec8fb1123e.jpg', 'image_id': 0}, {'id': 1, 'license': 1, 'file_name': 'frame133_13396

Casting the dataset:   0%|          | 0/281 [00:00<?, ? examples/s]

Dataset for test split:
Dataset({
    features: ['id', 'license', 'file_name', 'height', 'width', 'date_captured', 'extra', 'objects', 'image', 'image_id'],
    num_rows: 281
})
[{'id': 0, 'license': 1, 'file_name': 'frame106_106966ms_jpg.rf.7e912fd866841d117307daf95b976eab.jpg', 'height': 1080, 'width': 1920, 'date_captured': '2025-11-24T02:48:19+00:00', 'extra': {'name': 'frame106_106966ms.jpg'}, 'objects': {'id': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31], 'category_id': [10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 17, 17], 'bbox': [[964, 800, 144, 142], [967, 646, 132, 114], [986, 378, 137, 151], [1316, 587, 76, 87], [1375, 612, 84, 113], [1387, 807, 95, 93], [1487, 773, 123, 149], [1474, 897, 81, 87], [1362, 944, 150, 136], [1491, 523, 102, 185], [1687, 569, 99, 105], [1720, 261, 121, 139], [1783, 511, 118, 146], [1757, 777, 126, 131], [5

Casting the dataset:   0%|          | 0/551 [00:00<?, ? examples/s]

Dataset for valid split:
Dataset({
    features: ['id', 'license', 'file_name', 'height', 'width', 'date_captured', 'extra', 'objects', 'image', 'image_id'],
    num_rows: 551
})


In [ ]:
train_dataset = hf_dataset_dict['train']
valid_dataset = hf_dataset_dict['valid']
test_dataset = hf_dataset_dict['test']

In [ ]:
# quick check
train_dataset[0]['objects']

{'id': [1,
  2,
  3,
  4,
  5,
  6,
  7,
  8,
  9,
  10,
  11,
  12,
  13,
  14,
  15,
  16,
  17,
  18,
  19,
  20,
  21,
  22],
 'category_id': [10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  10,
  17],
 'bbox': [[635.0, 111.0, 62.0, 133.0],
  [616.0, 245.0, 119.0, 108.0],
  [772.0, 377.0, 82.0, 94.0],
  [846.0, 470.0, 131.0, 88.0],
  [782.0, 659.0, 97.0, 94.0],
  [661.0, 571.0, 124.0, 173.0],
  [542.0, 685.0, 9.0, 8.0],
  [403.0, 454.0, 110.0, 179.0],
  [499.0, 401.0, 184.0, 122.0],
  [587.0, 330.0, 74.0, 103.0],
  [478.0, 296.0, 69.0, 70.0],
  [533.0, 625.0, 153.0, 164.0],
  [289.0, 725.0, 106.0, 92.0],
  [424.0, 872.0, 75.0, 71.0],
  [485.0, 939.0, 110.0, 107.0],
  [78.0, 489.0, 143.0, 197.0],
  [1042.0, 880.0, 75.0, 74.0],
  [1282.0, 703.0, 68.0, 71.0],
  [1513.0, 580.0, 125.0, 127.0],
  [1573.0, 172.0, 138.0, 92.0],
  [1131.0, 333.0, 92.0, 140.0],
  [1690.0, 499.0, 198.0, 392.0]],
 'area': [8246.0,
  12852.

In [ ]:
# quick check
img = train_dataset[1]['image']
draw = ImageDraw.Draw(img)
for box, cat in zip(train_dataset[1]['objects']['bbox'], train_dataset[1]['objects']['category']):
    # COCO bbox format: [x_min, y_min, width, height]
    # ImageDraw.rectangle expects: [x_min, y_min, x_max, y_max]
    x_min, y_min, width, height = box
    x_max = x_min + width
    y_max = y_min + height
    draw.rectangle([x_min, y_min, x_max, y_max], outline='red', width=3) # Added width for better visibility
    draw.text((x_min, y_min-24), cat, font_size=24, fill='red')
img

In [ ]:
# data augmentation
# - Augment the dataset.
# - Rescale images to a maximum size, flip them, and apply affine transforms.
# - Eliminate invalid bounding boxes and ensure annotations stay clean with `rebuild_objects`.

train_aug = A.Compose(
    [
        # A.LongestMaxSize(max_size=1024, p=1.0),
        # A.HorizontalFlip(p=0.5),
        # A.Affine(rotate=(-5, 5), shear=(-5, 5), translate_percent=(0.05, 0.05), p=0.5),
        A.NoOp()
    ],
    bbox_params=A.BboxParams(format="coco", label_fields=["category_id"], min_visibility=0.0, filter_invalid_bboxes=True),
)

def train_transform(batch):
    imgs_out, objs_out = [], []
    original_imgs, original_objs = batch["image"], batch["objects"]

    for i, (img_pil, objs) in enumerate(zip(original_imgs, original_objs)):
        img = np.array(img_pil)
        labels = objs['category_id']

        out = train_aug(image=img, bboxes=list(objs["bbox"]), category_id=labels)

        if len(out["bboxes"]) == 0:
            imgs_out.append(img_pil) # if no boxes left after augmentation, use original
            objs_out.append(objs)
            continue

        H, W = out["image"].shape[:2]
        clamped = []
        for (x, y, w, h) in out["bboxes"]:
            x = max(0.0, min(x, W - 1.0))
            y = max(0.0, min(y, H - 1.0))
            w = max(1.0, min(w, W - x))
            h = max(1.0, min(h, H - y))
            clamped.append([x, y, w, h])

        # print(i, clamped)


        # for (x, y, w, h) in objs["bboxes"]:
        #     x_min, y_min, width, height = box
        #     x_max = x_min + width
        #     y_max = y_min + height

        imgs_out.append(Image.fromarray(out["image"]))
        objs_out.append(rebuild_objects(clamped, out["category_id"], objs['iscrowd']))
        # imgs_out.append(Image.fromarray(img))
        # objs_out.append(rebuild_objects(objs['bbox'], labels, objs['iscrowd']))

    batch["image"] = imgs_out
    batch["objects"] = objs_out
    return batch



def rebuild_objects(bboxes, labels, iscrowd_list):
    bboxes = [list(map(float, b)) for b in bboxes]
    areas  = [float(w*h) for (_, _, w, h) in bboxes]
    ids    = list(range(len(bboxes)))
    return {
        "id": ids,
        "bbox": bboxes,
        "category_id": list(map(int, labels)),
        "area": areas,
        "iscrowd": iscrowd_list
    }

train_dataset = train_dataset.with_transform(train_transform)

In [ ]:
# build COCO-style annotations for the image processor.
def format_annotations(image, objects, image_id, iscrowd_list):
    n = len(objects["id"])
    anns = []
    area_list = objects.get("area", None)

    for i in range(n):
        x, y, w, h = objects["bbox"][i]
        area = area_list[i] if area_list is not None else float(w * h)

        anns.append({
            "id": int(objects["id"][i]),
            "iscrowd": int(iscrowd_list[i]),
            "bbox": [float(x), float(y), float(w), float(h)],
            "category_id": int(objects.get("category_id", objects.get("category"))[i]),
            "area": float(area)
        })

    return {"image_id": int(image_id), "annotations": anns}

In [ ]:
# - Create batches in the data collator.
# - Format annotations and pass them with transformed images to the image processor.
def collate_fn(examples):
    images = [example["image"] for example in examples]
    ann_batch = [format_annotations(example["image"], example["objects"], example["image_id"], example['objects']['iscrowd']) for example in examples]

    inputs = image_processor(images=images, annotations=ann_batch, return_tensors="pt")
    return inputs

# Training

In [ ]:
training_args = TrainingArguments(
    output_dir=output_root,
    per_device_train_batch_size=32,
    per_device_eval_batch_size=32,
    num_train_epochs=50,
    learning_rate=1e-5,
    weight_decay=1e-4,
    warmup_steps=125,
    eval_strategy="steps",
    eval_steps=125,
    save_total_limit=2,
    dataloader_pin_memory=False,
    fp16=True,
    report_to="none",
    load_best_model_at_end=True,
    remove_unused_columns=False,
    push_to_hub=True,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=valid_dataset,
    data_collator=collate_fn,
)

In [ ]:
trainer.train()

TrainOutput(global_step=3050, training_loss=4.603604135982326, metrics={'train_runtime': 21671.4733, 'train_samples_per_second': 4.453, 'train_steps_per_second': 0.141, 'total_flos': 3.718368342738155e+20, 'train_loss': 4.603604135982326, 'epoch': 50.0})

In [ ]:
# resume training from checkpoint -> due to trackio bug
# trainer.train(resume_from_checkpoint='/content/drive/MyDrive/AIC Data/Project/output/checkpoint-1936')
trainer.train(resume_from_checkpoint=True)

ValueError: Can't find a valid checkpoint at /content/drive/MyDrive/AIC Data/Project/algae-detr-dinov3/checkpoint-1936

In [ ]:
trainer.push_to_hub()
image_processor.push_to_hub("poglicious/algae-detr-dinov3")

Processing Files (0 / 0)      : |          |  0.00B /  0.00B            

New Data Upload               : |          |  0.00B /  0.00B            

  ...-dinov3/training_args.bin: 100%|##########| 5.20kB / 5.20kB            

  ...-dinov3/model.safetensors:   3%|2         | 25.2MB /  857MB            

README.md: 0.00B [00:00, ?B/s]

No files have been modified since last commit. Skipping to prevent empty commit.


CommitInfo(commit_url='https://huggingface.co/poglicious/algae-detr-dinov3/commit/be994059c936f437333937cc95d1b68323903c97', commit_message='Upload processor', commit_description='', oid='be994059c936f437333937cc95d1b68323903c97', pr_url=None, repo_url=RepoUrl('https://huggingface.co/poglicious/algae-detr-dinov3', endpoint='https://huggingface.co', repo_type='model', repo_id='poglicious/algae-detr-dinov3'), pr_revision=None, pr_num=None)

# Test

In [ ]:
from transformers import pipeline

In [ ]:
obj_detector = pipeline(
    "object-detection", model="poglicious/algae-detr-dinov3", batch_size=16, device=0
)

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/857M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/449 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/785M [00:00<?, ?B/s]

Loading weights:   0%|          | 0/340 [00:00<?, ?it/s]

DINOv3ConvNextBackbone LOAD REPORT from: facebook/dinov3-convnext-large-pretrain-lvd1689m
Key                                                        | Status     |                                                                                 
-----------------------------------------------------------+------------+---------------------------------------------------------------------------------
layer_norm.bias                                            | UNEXPECTED |                                                                                 
layer_norm.weight                                          | UNEXPECTED |                                                                                 
stages.{0, 1, 2, 3}.downsample_layers.{0, 1}.bias          | MISC       | Parameter.__new__() got an unexpected keyword argument '_is_hf_initialized'
Erro
stages.{0, 1, 2, 3}.downsample_layers.{0, 1}.weight        | MISC       | Parameter.__new__() got an unexpected keyword argument '_is_h

Loading weights:   0%|          | 0/605 [00:00<?, ?it/s]

preprocessor_config.json:   0%|          | 0.00/455 [00:00<?, ?B/s]

Using a slow image processor as `use_fast` is unset and a slow processor was saved with this model. `use_fast=True` will be the default behavior in v4.52, even if the model was saved with a slow processor. This will result in minor differences in outputs. You'll still be able to use a slow processor with `use_fast=False`.


In [ ]:
img = train_dataset[8]['image']
results = obj_detector(img,
                       threshold=0.05)
print(results)

[{'score': 0.139909565448761, 'label': 'P. Amplifolius', 'box': {'xmin': 810, 'ymin': 550, 'xmax': 946, 'ymax': 683}}, {'score': 0.14024551212787628, 'label': 'P. Amplifolius', 'box': {'xmin': 809, 'ymin': 550, 'xmax': 944, 'ymax': 683}}, {'score': 0.14005044102668762, 'label': 'P. Amplifolius', 'box': {'xmin': 810, 'ymin': 550, 'xmax': 945, 'ymax': 683}}, {'score': 0.14003562927246094, 'label': 'P. Amplifolius', 'box': {'xmin': 810, 'ymin': 550, 'xmax': 945, 'ymax': 683}}, {'score': 0.14001904428005219, 'label': 'P. Amplifolius', 'box': {'xmin': 810, 'ymin': 550, 'xmax': 945, 'ymax': 683}}, {'score': 0.14000162482261658, 'label': 'P. Amplifolius', 'box': {'xmin': 810, 'ymin': 549, 'xmax': 945, 'ymax': 682}}, {'score': 0.14008332788944244, 'label': 'P. Amplifolius', 'box': {'xmin': 811, 'ymin': 550, 'xmax': 946, 'ymax': 683}}, {'score': 0.1399202048778534, 'label': 'P. Amplifolius', 'box': {'xmin': 810, 'ymin': 550, 'xmax': 946, 'ymax': 683}}, {'score': 0.13987353444099426, 'label': 'P

In [ ]:
from torchvision.ops import nms

def predict_images(images, threshold):
    # data = {"images": images}
    # dataset = Dataset.from_dict(data)
    results_list = obj_detector(images, threshold=threshold)

    output_list = []
    for results in results_list:
        if len(results) == 0:
            filtered_boxes = []
            filtered_scores = []
            filtered_labels = []
        else:
            boxes = torch.tensor([list(res["box"].values()) for res in results], dtype=torch.float32)
            scores = torch.tensor([res["score"] for res in results], dtype=torch.float32)
            labels = [res["label"] for res in results]

            keep_indices = nms(boxes, scores, iou_threshold=threshold)
            filtered_labels = [labels[i] for i in keep_indices]
            filtered_boxes = boxes[keep_indices].tolist()
            filtered_scores = scores[keep_indices]

        output_list.append({
            'labels': filtered_labels,
            'boxes': filtered_boxes,
            'scores': [float(fs) for fs in filtered_scores]
        })

        print(output_list)

    return output_list

def plot_results(image, boxes, scores, labels, threshold):
    image = image.copy()
    draw = ImageDraw.Draw(image)
    for bx, sc, label in zip(boxes, scores, labels):
        box = bx.tolist()
        score = float(sc)
        print(box, score)

        if score > threshold:
            x1, y1, x2, y2 = tuple(box)
            draw.rectangle((x1, y1, x2, y2), outline="red")
            draw.text((x1, y1-24), f"{label} {score:.2f}", font_size=24, fill="green" if score > 0.7 else "red")

    return image

def check_dataset_batch(dataset, threshold):
    total_result = []
    for i in range(0, len(dataset), 16):

        batch = dataset[i:i+16]['image']
        results = predict_images(batch, 0.05)
        total_result.extend(results)
    return total_result

In [ ]:
test_results = check_dataset_batch(test_dataset, 0.05)


[{'labels': [], 'boxes': [], 'scores': []}]
[{'labels': [], 'boxes': [], 'scores': []}, {'labels': [], 'boxes': [], 'scores': []}]
[{'labels': [], 'boxes': [], 'scores': []}, {'labels': [], 'boxes': [], 'scores': []}, {'labels': ['P. Amplifolius'], 'boxes': [[1069.0, 483.0, 1181.0, 617.0]], 'scores': [0.48314037919044495]}]
[{'labels': [], 'boxes': [], 'scores': []}, {'labels': [], 'boxes': [], 'scores': []}, {'labels': ['P. Amplifolius'], 'boxes': [[1069.0, 483.0, 1181.0, 617.0]], 'scores': [0.48314037919044495]}, {'labels': [], 'boxes': [], 'scores': []}]
[{'labels': [], 'boxes': [], 'scores': []}, {'labels': [], 'boxes': [], 'scores': []}, {'labels': ['P. Amplifolius'], 'boxes': [[1069.0, 483.0, 1181.0, 617.0]], 'scores': [0.48314037919044495]}, {'labels': [], 'boxes': [], 'scores': []}, {'labels': ['Clam Shell'], 'boxes': [[813.0, 546.0, 944.0, 688.0]], 'scores': [0.058620378375053406]}]
[{'labels': [], 'boxes': [], 'scores': []}, {'labels': [], 'boxes': [], 'scores': []}, {'labels

In [ ]:
try:
    with open('/content/drive/MyDrive/AIC Data/Project/test_results.json', 'w', encoding='utf-8') as f:
        json.dump(test_results, f, indent=4)
    print(f"List successfully written to '/content/drive/MyDrive/AIC Data/Project/test_results.json'")
except IOError as e:
    print(f"Error writing to file: {e}")

List successfully written to '/content/drive/MyDrive/AIC Data/Project/test_results.json'
